In [1]:
from google.transit import gtfs_realtime_pb2
import requests
from collections import defaultdict
import time
from datetime import datetime
import pandas as pd
from copy import deepcopy
import schedule
from ST_DBSCAN.stdbscan import STDBSCAN
import sys
from tqdm import tqdm
import folium
from folium.plugins import MarkerCluster
from folium.plugins import Search
from collections import Counter
route_dict = {}
# read entity data from protobuffer
def get_entity_data(entity):
    vehicle_id = entity.vehicle.vehicle.id
    vehicle_lat = entity.vehicle.position.latitude
    vehicle_lon = entity.vehicle.position.longitude
    vehicle_route_id = str(int(float(entity.vehicle.trip.route_id)))
    vehicle_timestamp = entity.vehicle.timestamp
    return vehicle_id, vehicle_lat, vehicle_lon, vehicle_route_id, vehicle_timestamp


def read_feed():
    # print(OTD_RT_URL)
    feed = gtfs_realtime_pb2.FeedMessage()
    try:
        response = requests.get(OTD_RT_URL)
        feed.ParseFromString(response.content)
        # print("Feed at " + str(datetime.datetime.now()))
    except TimeoutError:
        print("URL Timeout")
    except requests.exceptions.ConnectionError:
        print('Max retries exceeded')
    return feed

def read_routes():
    global route_dict
    routes = open('routes.txt','r')
    routes_data = routes.readlines()
    routes.close()
    
    for i in routes_data:
        i = i.split(',')
        route_dict[i[3]] = i[1]
    
    return route_dict

def run_db_scan(df, spatial_threshold=50, temporal_threshold=20, min_neighbors=12):
    if len(df) == 0:
        print(df)
    st_dbscan = STDBSCAN(col_lat='lat', col_lon='lng',
                         col_time='timestamp', spatial_threshold=spatial_threshold,
                         temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)
    df = st_dbscan.projection(df, p1_str='epsg:4326', p2_str='epsg:32635')
    result_t600 = st_dbscan.run(df)
    return result_t600


def save_to_dict():
    global remove_element_flag
    feed = read_feed()
    # print(feed)
    if time.time() - process_start_timestamp >= 1200:
        remove_element_flag = True
    for entity in feed.entity:
        # print(entity)
        vehicle_id, vehicle_lat, vehicle_lon, vehicle_route_id, vehicle_timestamp = get_entity_data(entity)
        if pb_data_dict.get(vehicle_id):
            if not (datetime.fromtimestamp(int(vehicle_timestamp)) in pb_data_dict[vehicle_id]['timestamp'] and vehicle_lat in pb_data_dict[vehicle_id]['lat'] and vehicle_lon in pb_data_dict[vehicle_id]['lng'] and vehicle_route_id in pb_data_dict[vehicle_id]['route_id']):
                pb_data_dict[vehicle_id]['lat'].append(vehicle_lat)
                pb_data_dict[vehicle_id]['lng'].append(vehicle_lon)
                pb_data_dict[vehicle_id]['timestamp'].append(datetime.fromtimestamp(int(vehicle_timestamp)))
                pb_data_dict[vehicle_id]['route_id'].append(vehicle_route_id)
                if remove_element_flag:
                    print('deleted for ', vehicle_id)
                    if len(pb_data_dict[vehicle_id]['lat']) <= 1:
                        del pb_data_dict[vehicle_id]
                    else:
                        pb_data_dict[vehicle_id]['lat'].pop(0)
                        pb_data_dict[vehicle_id]['lng'].pop(0)
                        pb_data_dict[vehicle_id]['timestamp'].pop(0)
                        pb_data_dict[vehicle_id]['route_id'].pop(0)
        else:
            vehicle_data_dict = defaultdict(list)
            vehicle_data_dict['lat'].append(vehicle_lat)
            vehicle_data_dict['lng'].append(vehicle_lon)
            vehicle_data_dict['timestamp'].append(datetime.fromtimestamp(int(vehicle_timestamp)))
            vehicle_data_dict['route_id'].append(vehicle_route_id)
            
            pb_data_dict[vehicle_id] = vehicle_data_dict
    # print(pb_data_dict)


def calculate_centroid(list_of_coordinates):
    return sum(list_of_coordinates)/len(list_of_coordinates)


def cluster_json_data(bus, pb_data_dict):
    global route_dict
    lat_list = pb_data_dict[bus]['lat']
    lng_list = pb_data_dict[bus]['lng']

    lat_centroid = calculate_centroid(lat_list)
    lng_centroid = calculate_centroid(lng_list)

#     timestamp = int(time.time())
    timestamp = pb_data_dict[bus]['timestamp'][-1]
    route_id = pb_data_dict[bus]['route_id'][0]
    route_dir = route_dict[route_id]

    bus_data = {'vehicle_id': bus, 'lat': lat_centroid, 'lng': lng_centroid, 'timestamp': timestamp, 'route_id' : route_id ,'route_direction':route_dir}

    return bus_data


def chk_cluster():
    global clustered_buses_list
    # production
    # spatial_threshold = 10
    # temporal_threshold = 900
    # min_neighbors = 90

    # testing (less time gap)
    spatial_threshold = 10
    temporal_threshold = 300
    min_neighbors = 30
    clustered_buses_data = []
    start = time.time()
    temp_list = list()
    print(len(pb_data_dict), "dict")
    for bus in tqdm(pb_data_dict.keys()):
        bus_data_df = pd.DataFrame.from_dict(pb_data_dict[bus])
#         return bus_data_df
        if len(bus_data_df) != 0:
            clustered_df = run_db_scan(deepcopy(bus_data_df), spatial_threshold=spatial_threshold,
                                       temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)
#             return clustered_df
            bus_data_df['cluster'] = clustered_df['cluster']
            # unique_clusters = chk_if_cluster_close_to_depot(bus_data_df)
            unique_clusters = pd.unique(bus_data_df.cluster)
#             return bus_data_df
            if len(unique_clusters) > 1:
                bus_data = cluster_json_data(bus,pb_data_dict)
#                 print('cluster detected for ',bus,bus_data)
#                 print(pb_data_dict[bus])
                clustered_buses_data.append(bus_data)
                temp_list.append(bus)
            else:
#                 print('no cluster detected for ', bus)
                pass
    clustered_buses_list = temp_list
#     print(clustered_buses_list)
#     print(time.time() - start)
    return clustered_buses_data

def plot_map():
    prob_buses = chk_cluster()
    start_lat = 28.617453756786528
    start_lon = 77.20423389616467

    m=folium.Map(location=[start_lat,start_lon],tiles='Open Street Map', zoom_start=10)
    for i in prob_buses:
    #     print(i)
        lat = i['lat']
        lng = i['lng']
        folium.Circle(
          location=[lat, lng],
          popup=i['vehicle_id'],
          color='crimson',
          fill=True,
          fill_color='crimson'
       ).add_to(m)
    m.save('map1.html')
    

if __name__ == '__main__':
    OTD_API_KEY = 'X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u'
    OTD_RT_URL = f'https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key={OTD_API_KEY}'
    print('OTD API URL', OTD_RT_URL)
    read_routes()
    pb_data_dict = {}
    clustered_buses_list = list()
    remove_element_flag = False
    process_start_timestamp = time.time()
    schedule.every(10).seconds.do(save_to_dict)
#     schedule.every(180).seconds.do(chk_cluster)
#     schedule.every(600).seconds.do(plot_map)
    counter = 0
    while counter < 600:
        schedule.run_pending()
        time.sleep(1)
        counter += 1
        print(counter)




OTD API URL https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key=X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
2

In [2]:
# OTD_API_KEY = 'X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u'
# OTD_RT_URL = f'https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key={OTD_API_KEY}'
# print('OTD API URL', OTD_RT_URL)

# pb_data_dict = {}
# clustered_buses_list = list()
# remove_element_flag = False
# process_start_timestamp = time.time()

In [4]:
# save_to_dict()

In [5]:
pb_data_dict

{'DL1PD5111': defaultdict(list,
             {'lat': [28.679393768310547,
               28.679393768310547,
               28.679393768310547,
               28.67938232421875,
               28.67938232421875,
               28.67938232421875,
               28.67938232421875,
               28.67938232421875,
               28.679378509521484,
               28.679161071777344,
               28.67904281616211,
               28.678974151611328,
               28.67893409729004,
               28.678808212280273,
               28.67865562438965,
               28.67852210998535,
               28.678428649902344,
               28.67833709716797,
               28.67819595336914,
               28.678165435791016,
               28.67788314819336,
               28.677736282348633,
               28.677701950073242,
               28.677701950073242,
               28.677480697631836,
               28.677270889282227,
               28.677066802978516,
               28.6767005920

In [6]:
prob_buses = chk_cluster()

2313 dict


100%|██████████████████████████████████████████████████████████████████████████████| 2313/2313 [00:27<00:00, 82.62it/s]


In [7]:
len(prob_buses)

101

In [8]:
prob_buses


[{'vehicle_id': 'DL1PD1178',
  'lat': 28.522277207210145,
  'lng': 77.08257083235115,
  'timestamp': datetime.datetime(2022, 4, 18, 12, 55, 11),
  'route_id': '64',
  'route_direction': '729DOWN'},
 {'vehicle_id': 'DL1PD5554',
  'lat': 28.66831232372083,
  'lng': 77.2257762708162,
  'timestamp': datetime.datetime(2022, 4, 18, 12, 44, 29),
  'route_id': '1113',
  'route_direction': '905ADOWN'},
 {'vehicle_id': 'DL1PC6716',
  'lat': 28.493928664769882,
  'lng': 77.30327977889624,
  'timestamp': datetime.datetime(2022, 4, 18, 12, 58, 10),
  'route_id': '560',
  'route_direction': '460CLUP'},
 {'vehicle_id': 'DL1PD5224',
  'lat': 28.634939567715513,
  'lng': 77.06217762068206,
  'timestamp': datetime.datetime(2022, 4, 18, 12, 58, 2),
  'route_id': '787',
  'route_direction': '890UP'},
 {'vehicle_id': 'DL1PC4831',
  'lat': 28.669638266930214,
  'lng': 77.13751748891977,
  'timestamp': datetime.datetime(2022, 4, 18, 12, 58, 4),
  'route_id': '70',
  'route_direction': '894CLUP'},
 {'vehicle_

In [9]:
cl1_bus_df = pd.DataFrame.from_dict(prob_buses)

In [10]:
cl1_bus_df['timestamp'] = pd.to_datetime(cl1_bus_df['timestamp'], unit = 's')

In [11]:
cl1_bus_df

vehicle_id        lat        lng           timestamp route_id  \
0    DL1PD1178  28.522277  77.082571 2022-04-18 12:55:11       64   
1    DL1PD5554  28.668312  77.225776 2022-04-18 12:44:29     1113   
2    DL1PC6716  28.493929  77.303280 2022-04-18 12:58:10      560   
3    DL1PD5224  28.634940  77.062178 2022-04-18 12:58:02      787   
4    DL1PC4831  28.669638  77.137517 2022-04-18 12:58:04       70   
..         ...        ...        ...                 ...      ...   
96   DL1PC6197  28.642633  77.223532 2022-04-18 12:58:09     1064   
97   DL1PD0836  28.521638  77.082068 2022-04-18 12:55:16       64   
98   DL1PC5507  28.660035  77.236247 2022-04-18 12:58:09      459   
99   DL1PD0627   3.486644   9.400842 2022-04-18 12:55:12      761   
100  DL1PC6448  28.615036  76.977827 2022-04-18 12:55:21      106   

    route_direction  
0           729DOWN  
1          905ADOWN  
2           460CLUP  
3             890UP  
4           894CLUP  
..              ...  
96         445ADOWN  
97          729DOWN  
98        214CLDOWN  
99          761DOWN  
100        818BDOWN  

[101 rows x 6 columns]

In [12]:
spatial_threshold = 300
temporal_threshold = 600
min_neighbors = 3
clustered_df2 = run_db_scan(deepcopy(cl1_bus_df), spatial_threshold=spatial_threshold,
                                       temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)

In [13]:
Counter(clustered_df2.cluster)

Counter({-1: 70, 1: 8, 2: 5, 3: 5, 4: 6, 5: 7})

In [14]:
clustered_df2

lng           lat           timestamp cluster
0    5.379838e+05  8.556479e+06 2022-04-18 12:55:11      -1
1    5.411732e+05  8.572553e+06 2022-04-18 12:44:29      -1
2    5.366505e+05  8.581083e+06 2022-04-18 12:58:10       1
3    5.408576e+05  8.554280e+06 2022-04-18 12:58:02      -1
4    5.414857e+05  8.562708e+06 2022-04-18 12:58:04      -1
..            ...           ...                 ...     ...
96   5.405466e+05  8.572285e+06 2022-04-18 12:58:09       2
97   5.379693e+05  8.556423e+06 2022-04-18 12:55:16      -1
98   5.409359e+05  8.573715e+06 2022-04-18 12:58:09      -1
99  -2.153367e+06  1.132062e+06 2022-04-18 12:55:12      -1
100  5.406188e+05  8.544857e+06 2022-04-18 12:55:21      -1

[101 rows x 4 columns]

In [15]:
cl1_bus_df['cluster'] = clustered_df2['cluster']
cl1_bus_df

vehicle_id        lat        lng           timestamp route_id  \
0    DL1PD1178  28.522277  77.082571 2022-04-18 12:55:11       64   
1    DL1PD5554  28.668312  77.225776 2022-04-18 12:44:29     1113   
2    DL1PC6716  28.493929  77.303280 2022-04-18 12:58:10      560   
3    DL1PD5224  28.634940  77.062178 2022-04-18 12:58:02      787   
4    DL1PC4831  28.669638  77.137517 2022-04-18 12:58:04       70   
..         ...        ...        ...                 ...      ...   
96   DL1PC6197  28.642633  77.223532 2022-04-18 12:58:09     1064   
97   DL1PD0836  28.521638  77.082068 2022-04-18 12:55:16       64   
98   DL1PC5507  28.660035  77.236247 2022-04-18 12:58:09      459   
99   DL1PD0627   3.486644   9.400842 2022-04-18 12:55:12      761   
100  DL1PC6448  28.615036  76.977827 2022-04-18 12:55:21      106   

    route_direction cluster  
0           729DOWN      -1  
1          905ADOWN      -1  
2           460CLUP       1  
3             890UP      -1  
4           894CLUP      -1  
..              ...     ...  
96         445ADOWN       2  
97          729DOWN      -1  
98        214CLDOWN      -1  
99          761DOWN      -1  
100        818BDOWN      -1  

[101 rows x 7 columns]

In [24]:
Counter(cl1_bus_df['cluster'])

Counter({-1: 70, 1: 8, 2: 5, 3: 5, 4: 6, 5: 7})

In [25]:
cl1_bus_df.loc[(cl1_bus_df['cluster'] == 4) , :]

vehicle_id        lat        lng           timestamp route_id  \
17  DL1PC6508  28.590309  77.238828 2022-04-18 12:58:09     1215   
28  DL1PC5814  28.590696  77.237736 2022-04-18 12:58:03      459   
32  DL1PC6375  28.590787  77.238934 2022-04-18 12:58:04       31   
44  DL1PC6337  28.590804  77.238920 2022-04-18 12:58:04     1016   
67  DL1PC6967  28.590412  77.238965 2022-04-18 12:58:12     1094   
72  DL1PC6532  28.590811  77.237891 2022-04-18 12:58:11      208   

   route_direction cluster  
17           185UP       4  
28       214CLDOWN       4  
32         548CLUP       4  
44       410CLDOWN       4  
67          181AUP       4  
72        624ACLUP       4

In [16]:
max_cluster_index = max(clustered_df2.cluster)

cluster_lat_centroid = [[] for i in range(max_cluster_index+1)]
cluster_lng_centroid = [[] for i in range(max_cluster_index+1)]

for ind in cl1_bus_df.index:
    if cl1_bus_df['cluster'][ind] != -1:
        cluster_lat_centroid[clustered_df2['cluster'][ind]] += [cl1_bus_df['lat'][ind]]
        cluster_lng_centroid[clustered_df2['cluster'][ind]] += [cl1_bus_df['lng'][ind]]

cluster_centroid = {}

for k in range(1,len(cluster_lat_centroid)):
    cluster_centroid[k] = {'lat': sum(cluster_lat_centroid[k])/len(cluster_lat_centroid[k]) ,'lng':sum(cluster_lng_centroid[k])/len(cluster_lng_centroid[k])}



In [17]:
cluster_centroid

{1: {'lat': 28.493964591390043, 'lng': 77.30321170418159},
 2: {'lat': 28.642215578994815, 'lng': 77.22378987310839},
 3: {'lat': 28.64629957426208, 'lng': 77.31515210148586},
 4: {'lat': 28.59063630246736, 'lng': 77.2385456336669},
 5: {'lat': 28.665241470624128, 'lng': 77.22510914968208}}

In [32]:
start_lat = 28.617453756786528
start_lon = 77.20423389616467

m=folium.Map(location=[start_lat,start_lon],tiles='Open Street Map', zoom_start=10)
for i in cluster_centroid:
#     print(i)
    lat = cluster_centroid[i]['lat']
    lng = cluster_centroid[i]['lng']
    folium.Circle(
      location=[lat, lng],
      popup='Cluster '+ str(i) +" " +str(cl1_bus_df.loc[(cl1_bus_df['cluster'] == i) , 'vehicle_id'].values),
      color='crimson',
      fill=True,
      fill_color='red',
      radius = 50
   ).add_to(m)
m